In [201]:
import pandas as pd
import altair as alt
import numpy as np
import scipy
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [245]:
raw_data_hr = pd.read_json('data_dump.json')
raw_data_hr.rename(columns={'raw_readings_ir':'ir', 'raw_readings_red':'red'}, inplace=True)
raw_data_hr = raw_data_hr.loc[(raw_data_hr['ir'] > 50000) & (raw_data_hr['red'] != 0)].reset_index(drop=True).reset_index()
raw_data_hr = raw_data_hr.loc[raw_data_hr.index<5000]
raw_data_hr #[['raw_readings_ir','raw_readings_red']]

index     ir  filtered_dc_ir    red  interm_readings_ir
0         0  55257    52816.662577  33874        1.016234e+05
1         1  61100    52427.192228  33827        2.258833e+05
2         2  60949    45069.524973  33788        3.626590e+05
3         3  60867    41101.073664  33776        4.364196e+05
4         4  60856    38911.824204  33813        4.777953e+05
...     ...    ...             ...    ...                 ...
4995   4995  59449     -115.887649  32856        1.191182e+06
4996   4996  59449     -110.093266  32856        1.191072e+06
4997   4997  59449     -104.588603  32856        1.190967e+06
4998   4998  59449      -99.359173  32856        1.190868e+06
4999   4999  59449      -94.391214  32856        1.190773e+06

[5000 rows x 5 columns]

In [246]:
raw_data_hr_melted = raw_data_hr.melt(value_vars=['ir','red'], id_vars='index')
raw_data_hr_melted

index variable  value
0         0       ir  55257
1         1       ir  61100
2         2       ir  60949
3         3       ir  60867
4         4       ir  60856
...     ...      ...    ...
9995   4995      red  32856
9996   4996      red  32856
9997   4997      red  32856
9998   4998      red  32856
9999   4999      red  32856

[10000 rows x 3 columns]

In [345]:
alt.Chart(raw_data_hr_melted).mark_line().encode(
    x='index',
    y=alt.Y('value:Q',
        scale=alt.Scale(domain=(10000, 65000))
    ),
    color='variable'
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [248]:
class dcFilter_t:
    def __init__(self):
        self.w = None
        self.result = None

def dc_filter(x, alpha=0.95):
    print(x.ir, x.name)
    if x.name ==0:
        prev_w = 0
    filtered = {'w':None, 'result': None}
    filtered['w'] = x.ir + alpha * prev_w ;
    filtered['result'] = filtered['w'] - prev_w;
    return filtered



In [249]:
def _wR(i, col):
    x_i = raw_data_hr_melted.loc[raw_data_hr_melted['variable'] == col, 'value'].loc[i]
    if i==0:
        return x_i
    return x_i + _wR(i-1, col)

def _w(x, col): 
    return _wR(int(x.name), col)

In [304]:
_filtered = {}

for i in raw_data_hr.index:
    _filtered[i] = {}
    if i==0:
        _filtered[i]['w_ir'] = raw_data_hr.loc[i, 'ir']
        _filtered[i]['result_ir'] = _filtered[i]['w_ir']
    else:
        _filtered[i]['w_ir'] = raw_data_hr.loc[i, 'ir'] + 0.95 * _filtered[i-1]['w_ir']
        _filtered[i]['result_ir'] = _filtered[i]['w_ir'] - _filtered[i-1]['w_ir']
        
for i in raw_data_hr.index:
    if i==0:
        _filtered[i]['w_red'] = raw_data_hr.loc[i, 'red']
        _filtered[i]['result_red'] = _filtered[i]['w_red']
    else:
        _filtered[i]['w_red'] = raw_data_hr.loc[i, 'red'] + 0.95 * _filtered[i-1]['w_red']
        _filtered[i]['result_red'] = _filtered[i]['w_red'] - _filtered[i-1]['w_red']

In [305]:
_filtered

{0: {'w_ir': 55257, 'result_ir': 55257, 'w_red': 33874, 'result_red': 33874},
 1: {'w_ir': 113594.15,
  'result_ir': 58337.149999999994,
  'w_red': 66007.3,
  'result_red': 32133.300000000003},
 2: {'w_ir': 168863.4425,
  'result_ir': 55269.29250000001,
  'w_red': 96494.935,
  'result_red': 30487.634999999995},
 3: {'w_ir': 221287.270375,
  'result_ir': 52423.82787499999,
  'w_red': 125446.18824999999,
  'result_red': 28951.253249999994},
 4: {'w_ir': 271078.90685625,
  'result_ir': 49791.636481250025,
  'w_red': 152986.8788375,
  'result_red': 27540.69058750001},
 5: {'w_ir': 318468.9615134375,
  'result_ir': 47390.05465718749,
  'w_red': 179268.534895625,
  'result_red': 26281.656058124994},
 6: {'w_ir': 363643.5134377656,
  'result_ir': 45174.55192432809,
  'w_red': 204313.10815084373,
  'result_red': 25044.57325521874},
 7: {'w_ir': 406661.3377658773,
  'result_ir': 43017.82432811172,
  'w_red': 228176.45274330155,
  'result_red': 23863.34459245781},
 8: {'w_ir': 447589.2708775834,

In [339]:
filtered = pd.DataFrame(_filtered).transpose()
filtered = filtered.loc[(filtered.index>500) ].reset_index(drop=True).reset_index()
filtered['median_filter_ir'] = scipy.signal.medfilt(filtered['result_ir'], 9)
#butter
b, a = scipy.signal.butter(1, 10/100, 'low', fs=100, output='ba')
filtered['butterworth_red'] = scipy.signal.filtfilt(b, a, filtered['result_red'])
filtered

index          w_ir   result_ir          w_red  result_red  \
0         0  1.213784e+06  -43.342503  670269.718864  -15.248361   
1         1  1.213742e+06  -41.175378  670255.232921  -14.485943   
2         2  1.214261e+06  518.883391  670531.471274  276.238354   
3         3  1.214235e+06  -26.060778  670500.897711  -30.573564   
4         4  1.214210e+06  -24.757739  670471.852825  -29.044886   
...     ...           ...         ...            ...         ...   
4494   4494  1.191182e+06 -115.887649  657287.669132   -8.824691   
4495   4495  1.191072e+06 -110.093266  657279.285675   -8.383457   
4496   4496  1.190967e+06 -104.588603  657271.321391   -7.964284   
4497   4497  1.190868e+06  -99.359173  657263.755322   -7.566070   
4498   4498  1.190773e+06  -94.391214  657256.567556   -7.187766   

      median_filter_ir  butterworth_red  
0             0.000000         4.088264  
1           -23.519852         4.153378  
2           -23.519852         4.216366  
3           -23.519852         4.274513  
4           -23.519852         4.330992  
...                ...              ...  
4494        -97.589980       -21.752816  
4495        -94.391214       -21.749728  
4496        -94.391214       -21.747169  
4497        -94.391214       -21.745153  
4498        -94.391214       -21.743696  

[4499 rows x 7 columns]

In [340]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='result_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [375]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='result_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [352]:
alt.Chart(filtered.loc[(filtered.index>540) & (filtered.index<2380)]).mark_line().encode(
    x='index',
    y='median_filter_ir',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [366]:
x = filtered.loc[(filtered.index>540) & (filtered.index<2380)]
x

index          w_ir   result_ir          w_red  result_red  \
541     541  1.226639e+06 -160.992567  673572.098716  -55.373617   
542     542  1.226486e+06 -152.942939  673519.493780  -52.604936   
543     543  1.225956e+06 -530.295792  673358.519091 -160.974689   
544     544  1.225741e+06 -214.781002  673300.593137  -57.925955   
545     545  1.225537e+06 -204.041952  673245.563480  -55.029657   
...     ...           ...         ...            ...         ...   
2375   2375  1.208708e+06 -268.859398  664176.727755  -74.564619   
2376   2376  1.208453e+06 -255.416428  664105.891367  -70.836388   
2377   2377  1.208210e+06 -242.645607  664038.596799  -67.294568   
2378   2378  1.207980e+06 -230.513327  663974.666959  -63.929840   
2379   2379  1.207761e+06 -218.987660  663913.933611  -60.733348   

      median_filter_ir  butterworth_red  
541        -187.773806       -11.665568  
542        -187.773806       -11.686558  
543        -184.147862       -11.704836  
544        -184.147862       -11.719307  
545        -193.839854       -11.730965  
...                ...              ...  
2375       -230.513327        -8.741488  
2376       -242.645607        -8.733131  
2377       -246.936363        -8.722320  
2378       -246.936363        -8.709195  
2379       -242.645607        -8.693888  

[1839 rows x 7 columns]

In [370]:
i_rms_red = np.sqrt(x['result_red'].apply(lambda j: j*j).sum()/len(x))
i_rms_ir = np.sqrt(x['result_ir'].apply(lambda j: j*j).sum()/len(x))

In [372]:
R = (i_rms_red * 650) / (i_rms_ir * 950) 
R

0.20847023601373035

In [374]:
110 -  * R

72.47535751752854

In [353]:
filtered.loc[(filtered.index>540) & (filtered.index<2380)]

index          w_ir   result_ir          w_red  result_red  \
541     541  1.226639e+06 -160.992567  673572.098716  -55.373617   
542     542  1.226486e+06 -152.942939  673519.493780  -52.604936   
543     543  1.225956e+06 -530.295792  673358.519091 -160.974689   
544     544  1.225741e+06 -214.781002  673300.593137  -57.925955   
545     545  1.225537e+06 -204.041952  673245.563480  -55.029657   
...     ...           ...         ...            ...         ...   
2375   2375  1.208708e+06 -268.859398  664176.727755  -74.564619   
2376   2376  1.208453e+06 -255.416428  664105.891367  -70.836388   
2377   2377  1.208210e+06 -242.645607  664038.596799  -67.294568   
2378   2378  1.207980e+06 -230.513327  663974.666959  -63.929840   
2379   2379  1.207761e+06 -218.987660  663913.933611  -60.733348   

      median_filter_ir  butterworth_red  
541        -187.773806       -11.665568  
542        -187.773806       -11.686558  
543        -184.147862       -11.704836  
544        -184.147862       -11.719307  
545        -193.839854       -11.730965  
...                ...              ...  
2375       -230.513327        -8.741488  
2376       -242.645607        -8.733131  
2377       -246.936363        -8.722320  
2378       -246.936363        -8.709195  
2379       -242.645607        -8.693888  

[1839 rows x 7 columns]

In [342]:
alt.Chart(filtered).mark_line().encode(
    x='index',
    y='butterworth_red',
).properties(
    width=1000,
    height=400
)

alt.Chart(...)

In [344]:
source

symbol       date   price
0     MSFT 2000-01-01   39.81
1     MSFT 2000-02-01   36.35
2     MSFT 2000-03-01   43.22
3     MSFT 2000-04-01   28.37
4     MSFT 2000-05-01   25.45
..     ...        ...     ...
555   AAPL 2009-11-01  199.91
556   AAPL 2009-12-01  210.73
557   AAPL 2010-01-01  192.06
558   AAPL 2010-02-01  204.62
559   AAPL 2010-03-01  223.02

[560 rows x 3 columns]